In [1]:
import plotly.graph_objects as go

from math import log, isnan
import numpy as np
from scipy.constants import pi, Avogadro, hbar, m_e, e, epsilon_0, eV


In [2]:
from scimath.units.api import UnitScalar, UnitArray, convert, has_units
from scimath.units.energy import J, eV, KeV
from scimath.units.electromagnetism import coulomb, farad
from scimath.units.length import m, cm, km, angstrom
from scimath.units.time import s
from scimath.units.mass import g, kg
from scimath.units.density import g_per_cm3, kg_per_m3
from scimath.units.substance import mol
from scimath.units.dimensionless import dim

### Scattering variables for Al

In [3]:
# number of valence electrons
n_val_Al = 3

E_val_Al = UnitScalar(72.55, units="eV")

# energy levels for core electrons
name_s_Al = ['1s', '2s', '2p']
# binding energies
Ei_Al = UnitArray((1559, 118, 73.5), units="eV")
# number of electrons per shell
ni_Al = np.array([2, 2, 6])

Z_Al = 13
density_Al = UnitScalar(2.70, units="g_per_cm3")
atwt_Al = UnitScalar(26.98154, units="g/mol")

# modified Bethe k value from Joy and Luo, Scanning 1989
k_Al = 0.815

# incident energy
E_Al = UnitScalar(20000, units="eV")
# 5..100
Ec_Al = UnitScalar(10., units="eV")


### Scattering variables for Si

In [4]:
# number of valence electrons
n_val_Si = 4

E_val_Si = UnitScalar(99.42, units="eV")

# energy levels for core electrons
name_s_Si = ['1s', '2s', '2p']
# binding energies
Ei_Si = UnitArray((1189, 149, 100), units="eV")
# number of electrons per shell
ni_Si = np.array([2, 2, 6])

Z_Si = 14
density_Si = UnitScalar(2.33, units="g_per_cm3")
atwt_Si = UnitScalar(28.085, units="g/mol")

# modified Bethe k value from Joy and Luo, Scanning 1989
k_Si = 0.822

# incident energy
E_Si = UnitScalar(20000, units="eV")
# 5..100
Ec_Si = UnitScalar(10., units="eV")

### Scattering variables for Cu

In [5]:
# number of valence electrons
n_val_Cu = 11

E_val_Cu = UnitScalar(75.1, units="eV")

# energy levels for core electrons
name_s_Cu = ['1s', '2s2p', '3s', '3p']
# binding energies
Ei_Cu = UnitArray((8980, 977, 120, 74), units="eV")
# number of electrons per shell
ni_Cu = np.array([2, 8, 2, 6])

Z_Cu = 29
density_Cu = UnitScalar(8.96, units="g_per_cm3")
atwt_Cu = UnitScalar(63.546, units="g/mol")

# modified Bethe k value from Joy and Luo, Scanning 1989
k_Cu = 0.83

# incident energy
E_Cu = UnitScalar(20000, units="eV")
# 5..100
Ec_Cu = UnitScalar(10., units="eV")

### Scattering variables for Au

In [6]:
# number of valence electrons
n_val_Au = 11

# energy levels for core electrons
name_s_Au = ['2s2p', '3s3p3d', '4s4p', '4d', '5s', '4f', '5p2', '5p4']
# binding energies
Ei_Au = UnitArray((12980, 2584, 624, 341, 178, 85, 72, 54), units="eV")
# number of electrons per shell
ni_Au = np.array([8, 18, 8, 10, 2, 14, 2, 4])

Z_Au = 79
density_Au = UnitScalar(19.30, units="g_per_cm3")
atwt_Au = UnitScalar(196.967, units="g/mol")

# modified Bethe k value from Joy and Luo, Scanning 1989
k_Au = 0.851

# incident energy
E_Au = UnitScalar(20000, units="eV")
# 5..100
Ec_Au = UnitScalar(10., units="eV")

In [7]:
@has_units
def at_num_dens(dens, atom_mass):
    """ Calculate the atomic number density for given 
        density and atomic mass/weight
        
        Parameters
        ----------
        dens      : array : units = g_per_cm3

        atom_mass : array : units = g/mol
        
        Returns
        -------
        n         : array : units = m**-3
                   n = dens*A/atom_mass                 
      """
    A = Avogadro
    n = dens*A/atom_mass * cm**-3/m**-3
    return n


@has_units
def fermi_energy(atNumDens, nvalence, u_hbar, u_me):
    """ Calculate the Fermi energy of a material
        from its density, atomic weight and
        the number of valence electrons
        
        Parameters
        ----------
        atNumDens : array  : units = m**-3
        
        u_hbar    : scalar : units = J*s
        
        u_me      : scalar : units = kg
        
        Returns
        -------
        Ef        : array : units = eV
                    Ef = hbar**2 * (3.*(pi**2)*n)**(2./3.)/(2.*me)              
      """

    n = nvalence * atNumDens
    
    Ef = u_hbar**2 * (3.*(pi**2)*n)**(2./3.)/(2.*u_me) * m**2*kg*s**-2/ eV
    return Ef
    
    
@has_units
def plasmon_energy(atNumDens, nvalence, u_hbar, u_me, u_e, u_eps0):
    """ Calculate the plasmon energy of a material
        from its density, atomic weight and
        the number of valence electrons
        
        Parameters
        ----------
        atNumDens : array  : units = m**-3
        
        u_hbar    : scalar : units = J*s
        
        u_me      : scalar : units = kg
        
        u_e       : scalar : units = coulomb
        
        u_eps0    : scalar : units = farad*m**-1
        
        Returns
        -------
        Epl        : array : units = eV
                    Ef = hbar * ((n * e**2)/(u_eps0 * u_me))**0.5              
      """   
    
    n = nvalence * atNumDens

    Epl = u_hbar * e * (n/(u_eps0 * u_me))**0.5  * (m**2 * kg * s**-2)/ eV
    return Epl



# some constants    
u_hbar = UnitScalar(hbar, units="J*s")
u_me = UnitScalar(m_e, units="kg")
u_e    = UnitScalar(e, units="coulomb")
u_eps0 = UnitScalar(epsilon_0, units="farad*m**-1")

atnumdens = at_num_dens(density_Al, atwt_Al) 
c_pi_efour = UnitScalar(6.51408491409531e-14, units="cm**2 * eV**2")
#print 'atomic number density:', atnumdens 
#print 'Fermi energy:', fermi_energy(atnumdens, n_val_Al, u_hbar, u_me)
#print 'plasmon energy:', plasmon_energy(atnumdens, n_val_Al, u_hbar, u_me, u_e, u_eps0)

#print  m**2 * kg * s**-2/ eV

## Total cross sections, $\sigma$

#### 1a) Elastic Rutherford scattering cross section

In [8]:
@has_units
def ruther_sigma(E, Z):
    """ Calculate the Rutherford elastic cross section
        per atom
        
        Parameters
        ----------
        E      : array : units = KeV
        
        Z      : array : units = dim        
        
        Returns
        -------
        s_R    : array : units = cm**2       
    """      
    alpha =  3.4e-3*(Z**(0.67))/E 
    s_R = 5.21e-21 * (Z**2/(E**2)) * (4.*pi)/(alpha*(1. + alpha)) * ((E + 511.)/(E + 1024.))**2 
    return s_R

@has_units
def ruther_N_sigma_wDefl(E, Z, c_pi_efour):
    """ Calculate the Rutherford elastic cross section
        per atom

        Parameters
        ----------
        E      : array : units = eV

        Z      : array : units = dim

        c_pi_efour: scalar: units = cm**2 * eV**2

        Returns
        -------
        s_R    : array : units = cm**2
    """

    beta_N = 5.43 * Z**(2/3)/E

    # this value has been tweaked by fitting Rutherford CS to the pwem model
    # see Adesida, Schimizu, Everhart (1980) JAP 51 (11)
    beta_N_star = 0.48*beta_N

    # correction factor for angular deflection of inelastic scattering
    # Z**2 - > Z*(Z + 1)
    s_R = c_pi_efour * (Z+1)*Z/ (4*beta_N_star*(1+beta_N_star)*E**2)
    return s_R

print ('mean free path is in the range:', atwt_Al/(ruther_sigma(E_Al, 18)* Avogadro* density_Al)*1e8, 'Angstroms')                     
print ('with Nigraru correction and accounting for deflection', atwt_Al/(ruther_N_sigma_wDefl(E_Al, 20, c_pi_efour)* Avogadro* density_Al)*1e8, 'Angstroms')
#print ruther_sigma(E_Al, 13)

mean free path is in the range: UnitScalar (0.01*m*mol**-1): 142.76593785489837 Angstroms
with Nigraru correction and accounting for deflection UnitScalar (0.01*m*mol**-1): 93.27184141846185 Angstroms


#### 2a) Inelastic Moller cross section for free electrons

In [10]:
@has_units
def moller_sigma(E, Emin, nfree, c_pi_efour):
    """ Calculate the Moller inelastic cross section
        per atom
        
        Parameters
        ----------
        E      : array : units = eV
        
        Emin   : array : units = eV        
        
        nfree  : array : units = dim
        
        c_pi_efour: scalar: units = cm**2 * eV**2
        
        Returns
        -------
        s_M    : array : units = cm**2       
    """  
    
    eps = Emin*1./E
    s_M = nfree*c_pi_efour*(1./(E*E)) * (1./eps - 1./(1.-eps) + np.log(eps/(1.-eps)))
    return s_M

sigma_e = UnitArray(np.linspace(Ec_Al, E_Al, 1000), units="eV")
c_pi_efour = UnitScalar(6.51408491409531e-14, units="cm**2 * eV**2")

#print moller_sigma(sigma_e[1:], Ec_Al, n_val_Al, c_pi_efour)

#### 2b) Inelastic Gryzinski cross section for core shell electrons

In [11]:
@has_units
def gryz_sigma(E, Enl, nsi, c_pi_efour):
    """ Calculate the Moller inelastic cross section
        per atom
        
        Parameters
        ----------
        E      : array : units = eV
        
        Enl    : array : units = eV 
        
        nsi    : array : units = dim
                 number of electrons in i-shell
        c_pi_efour: scalar: units = cm**2 * eV**2
         
        Returns
        -------
        s_G    : array : units = cm**2       
    """ 
    
    U = E*1./Enl
    s_G = nsi * c_pi_efour * ((U - 1.)/(U + 1.))**1.5 * (1. + (2.*(1.-(1./(2.*U)))/3. * 
              np.log(2.7 + ((U-1.)**0.5))) ) /(E*Enl)
    return s_G

@has_units
def gryz_sigma_P(E, Enl, nnl, c_pi_efour):
    """ Calculate the Moller inelastic cross section
        per atom
        
        Parameters
        ----------
        E      : array : units = eV
        
        Enl    : scalar : units = eV    
        
        c_pi_efour: scalar: units = cm**2 * eV**2
         
        Returns
        -------
        s_G    : array : units = cm**2       
    """ 
    s_G = nnl * c_pi_efour *((E-Enl)/(E + Enl))**1.5 *(1. + (2.*(1.- Enl/(2.*E))*
                                            np.log(2.7 + (-1. + E/Enl)**0.5))/3.)/(E*Enl)
    return s_G


  
sigma_e = UnitArray(np.linspace(float(Ec_Al), float(E_Al), 1000), units="eV")

c_pi_efour = UnitScalar(6.51408491409531e-14, units="cm**2 * eV**2")

#print gryz_sigma(sigma_e[1:], Ei_Al[0], ni_Al[0], c_pi_efour)
#print gryz_sigma_P(sigma_e[1:], Ei_Al[0], ni_Al[0], c_pi_efour)

#### 2c) Inelastic Quinn cross section for plasmons

In [12]:
@has_units
def quinn_sigma(E, Epl, Ef, n, bohr_r):
    """ Calculate the Quinn inelastic cross section
        per atom 
        
        Parameters
        ----------
        E      : array : units = eV
                incident energy
                
        Epl    : array : units = eV        
                plasmon energy
        
        Ef     : array : units = eV        
                Fermi energy
                
        n      : array : units = m**-3
               number density
        
        bohr_r :scalar : units = m
        
        Returns
        -------
        s_Q    : array : units = cm**2       
    """     
    E_Ef = E*1./Ef
    Epl_Ef = Epl*1./Ef
    
    #print E, Epl, Ef, E_Ef, Epl_Ef
    s_Q_total = Epl*np.log( ((1. + Epl_Ef)**(0.5) - 1.)/ ( E_Ef**0.5 - 
             (E_Ef - Epl_Ef)**0.5 ) )/(2. *  bohr_r * E) 
    s_Q = s_Q_total/n * m**2/ cm**2
    
    return s_Q

@has_units
def quinn_mfp(E, Epl, Ef, bohr_r):
    """ Calculate the Quinn inelastic mean free path
        for plasmon scattering
        Parameters
        ----------
        E      : array : units = eV
                incident energy
                
        Epl    : array : units = eV        
                plasmon energy
        
        Ef     : array : units = eV        
                Fermi energy
        
        bohr_r :scalar : units = m
        Returns
        -------
        mfp_Q   : array : units = angstrom       
    """ 
    E_Ef = E*1./Ef
    Epl_Ef = Epl*1./Ef
    
    mfp_Q = 2.*bohr_r*E/Epl*(np.log(((1. + Epl_Ef)**0.5 - 1.)/
                        ((E_Ef)**0.5 - (E_Ef - Epl_Ef)**0.5)))**(-1.) * m/angstrom 
    return mfp_Q

@has_units
def quinn_mfp_P(E, Epl, Ef, bohr_r):
    """ Calculate the Quinn inelastic mean free path
        for plasmon scattering
        Parameters
        ----------
        E      : array : units = eV
                incident energy
                
        Epl    : array : units = eV        
                plasmon energy
        
        Ef     : array : units = eV        
                Fermi energy
        
        bohr_r :scalar : units = m
        Returns
        -------
        mfp_Q   : array : units = angstrom       
    """ 
    x = (E/Ef)**0.5
    y = Epl/Ef
    # the power 2 in 2d2 is for converting from m to cm
    mfp_Q = 2.*bohr_r*E/Epl*(np.log(((1. + y)**0.5 - 1.)/
                                     (x-(x**2 - y)**0.5)))**(-1) * m/angstrom 
    return mfp_Q


@has_units
def quinn_sigma_from_mfp(mfp_Q, n):
    """ Calculate the Quinn inelastic cross section
        
        Parameters
        ----------
        mfp_Q  : array : units = angstrom
                mean free path
                        
        n      : array : units = m**-3
        
        Returns
        -------
        s_Q    : array : units = cm**2       
    """     
    s_Q = 1./(n*mfp_Q) * m**3/angstrom/cm**2
    return s_Q


bohr_r = UnitScalar(5.2917721067e-11, units="m")
n_Al = at_num_dens(density_Al, atwt_Al)
Epl =  plasmon_energy(n_Al, n_val_Al, u_hbar, u_me, u_e, u_eps0)
Ef = fermi_energy(n_Al, n_val_Al,u_hbar, u_me)

Etest = UnitScalar(20000, units="eV")
#print  m**2*kg*s**-2/ eV
#print quinn_sigma(Etest, Epl, Ef, n_Al, bohr_r)
#print quinn_sigma(20000, Epl, Ef, n_Al, bohr_r)
#print quinn_mfp(10000, Epl, Ef, bohr_r)

### 2d) Tougaard universal cross section -- plasmon scatterting at low energy ($E<2keV$); for noble and transition metals

In [13]:
#@has_units
#def toug_sigma(E, W, B, C):
#    """ Calculate the Tougaard inelastic cross section
#        
#        Parameters
#        ----------
#        E      : array : units = eV**2
#                
#                        
#        n      : array : units = m**-3
#        
#        Returns
#        -------
#        s_Q    : array : units = cm**2       
#    """     
#    
#    return s_T

In [14]:
# array of energies
sigma_e = UnitArray(np.linspace(1000, 100000, 1000), units="eV")

# Plasmon inelastic mean free path
t_mfp_Quinn_P = go.Scatter(
    x = np.array(sigma_e[1:]),
    y = np.array(quinn_mfp_P(sigma_e[1:], Epl, Ef, bohr_r)),
    mode = 'lines', 
    name = 'plasmon mfp Patrick', 
    #marker = dict(color='#d9f0a3'
               #)
)

t_mfp_Quinn_E = go.Scatter(
    x = np.array(sigma_e[1:]),
    y = np.array(quinn_mfp(sigma_e[1:], Epl, Ef, bohr_r)),
    mode = 'lines', 
    name = 'plasmon mfp Elena', 
   # marker = dict(color='#d9f0a3'
          #     )
)

data = [t_mfp_Quinn_P, t_mfp_Quinn_E]

layout = go.Layout(
    title = 'plasmon mean free path in Al', 
    font=dict( color='#7f7f7f'),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',

    xaxis=dict(
        gridcolor= '#7f7f7f', 
        #range=[0.,E_Al],
        type='log',
        #autorange=True,
        title = 'E (eV)'
    ), 
    yaxis=dict(
        gridcolor= '#7f7f7f', 
        #autorange = False,
        #range = [0, 1.0e-17],
        type='log',
        title = 'mfp (A)'
    )
)

fig = go.Figure(data=data, layout=layout)

fig.show()

### Plot sigmas

In [24]:
# array of energies
sigma_e = UnitArray(np.linspace(Ec_Si, E_Si, 1000), units="eV")

schmzu_c = density_Al*Avogadro/100
print ('contant used in Schimizu 1976 for total cross section in Fig. 4', schmzu_c)
t_sigma_Ruth = go.Scatter(
    x = np.array(sigma_e[1:])/1000,
    y = np.array(ruther_sigma(sigma_e[1:], Z_Al)),
    mode = 'lines', 
    name = 'elastic', 
    marker = dict(color='#fcc5c0'
               )  
)

t_sigma_Moller = go.Scatter(
    x = np.array(sigma_e[1:])/1000,
    y = np.array(moller_sigma(sigma_e[1:], Ec_Si, n_val_Si, c_pi_efour)),
    mode = 'lines', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)


t_sigma_Gryz = []
widths = [3, 2, 1]

for indx, Eb in enumerate(list(Ei_Si)):
    nameT = "inner shell" + name_s_Si[indx]
    t_sigma_Gryz.append(go.Scatter(
        x = np.array(sigma_e[1:])/1000,
        y = np.array(gryz_sigma(sigma_e[1:], Ei_Si[indx], ni_Si[indx],c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                      width = widths[indx]
                     )
          ))

t_sigma_Gryz_P = []
for indx, Eb in enumerate(list(Ei_Si)):
    nameT = "inner shell P" + name_s_Al[indx]
    t_sigma_Gryz_P.append(go.Scatter(
        x = np.array(sigma_e[1:]),
        y = np.array(gryz_sigma_P(sigma_e[1:], Ei_Al[indx], ni_Al[indx],c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                      width = widths[indx]
                     )
          ))
    
    

bohr_r = UnitScalar(5.2917721067e-11, units="m")
n = at_num_dens(density_Si, atwt_Si)
Epl =  plasmon_energy(n, n_val_Si, u_hbar, u_me, u_e, u_eps0)
Ef = fermi_energy(n, n_val_Si,u_hbar, u_me)

mfp_Q = quinn_mfp(sigma_e[1:], Epl, Ef, bohr_r)

t_sigma_Quinn = go.Scatter(
    x = np.array(sigma_e[1:]/1000),
    y = np.array(quinn_sigma(sigma_e[1:], Epl, Ef, n, bohr_r)),
    mode = 'lines', 
    name = 'plasmon', 
    marker = dict(color='#fed976'
                 )
)



data = [t_sigma_Ruth, t_sigma_Moller, t_sigma_Gryz[0], t_sigma_Gryz[1], t_sigma_Gryz[2],
        t_sigma_Quinn]

layout = go.Layout(
    title = 'scattering cross sections per atom in Si', 
    width=500, height=600,showlegend=False,
#     font=dict( color='#7f7f7f'),
#     paper_bgcolor='rgba(0,0,0,0)',
#     plot_bgcolor='rgba(0,0,0,0)',

    xaxis=dict(
#         gridcolor= '#7f7f7f', 
        range=[3,20],
        #type='log',
        #autorange=True,
        title = 'E (keV)'
    ), 
    yaxis=dict(
#         gridcolor= '#7f7f7f', 
        #autorange = False,
        #range = [0, 1.0e-17],
        type='log',
        title = 'sigma (cm^2/atom)'
    )
)


fig = go.Figure(data=data, layout=layout)

#fig.show()
fig.write_image("images/crossSections_small.svg")

contant used in Schimizu 1976 for total cross section in Fig. 4 UnitScalar (g_per_cm3): 1.62597803139e+22


/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:23: RuntimeWarning:

invalid value encountered in power

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:23: RuntimeWarning:

invalid value encountered in sqrt

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:44: RuntimeWarning:

invalid value encountered in power

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:44: RuntimeWarning:

invalid value encountered in sqrt



In [25]:
dens = float(density_Al)

t_sigma_Ruth = go.Scatter(
    x = np.array(sigma_e[1:]),
    y = dens*Avogadro*np.array(ruther_sigma(sigma_e[1:], Z_Al)),
    mode = 'lines', 
    name = 'elastic', 
    marker = dict(color='#fcc5c0'
               )  
)

t_sigma_Moller = go.Scatter(
    x = np.array(sigma_e[1:]),
    y = dens*Avogadro*np.array(moller_sigma(sigma_e[1:], 10, n_val_Al, c_pi_efour)),
    mode = 'lines', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)


t_sigma_Gryz = []
widths = [3, 2, 1]

for indx, Eb in enumerate(list(Ei_Al)):
    nameT = "inner shell" + name_s_Al[indx]
    t_sigma_Gryz.append(go.Scatter(
        x = np.array(sigma_e[1:]),
        y = Avogadro*dens*np.array(gryz_sigma(sigma_e[1:], Ei_Al[indx], ni_Al[indx],c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                      width = widths[indx]
                     )
          ))


bohr_r = UnitScalar(5.2917721067e-11, units="m")
n = at_num_dens(density_Al, atwt_Al)
Epl =  plasmon_energy(n, n_val_Al, u_hbar, u_me, u_e, u_eps0)
Ef = fermi_energy(n, n_val_Al,u_hbar, u_me)

mfp_Q = quinn_mfp(sigma_e[1:], Epl, Ef, bohr_r)

t_sigma_Quinn = go.Scatter(
    x = np.array(sigma_e[1:]),
    y = Avogadro*dens*np.array(quinn_sigma_from_mfp(mfp_Q, n)),
    mode = 'lines', 
    name = 'plasmon', 
    marker = dict(color='#fed976'
                 )
)



data = [t_sigma_Ruth, t_sigma_Moller, t_sigma_Gryz[0], t_sigma_Gryz[1], t_sigma_Gryz[2], t_sigma_Quinn]

layout = go.Layout(
    title = 'scattering cross sections per density in Al', 
    font=dict( color='#7f7f7f'),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',

    xaxis=dict(
        gridcolor= '#7f7f7f', 
        range=[0.,E_Al],
        #type='log',
        #autorange=True,
        title = 'E (eV)'
    ), 
    yaxis=dict(
        gridcolor= '#7f7f7f', 
        #autorange = False,
        #range = [0, 1.0e-17],
        type='log',
        title = 'sigma (g/cm)'
    )
)


fig = go.Figure(data=data, layout=layout)

fig.show()

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:23: RuntimeWarning:

invalid value encountered in power

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:23: RuntimeWarning:

invalid value encountered in sqrt



## Excitation function $\frac{d\sigma}{d\Delta W}$ <cm**2/eV>

#### 2a) Moller differential cross section for free electrons

In [26]:
# Moller free electron discrete cross section
@has_units
def moller_dCS(E, W, nfree, c_pi_efour):
    """ Calculate the Moller inelastic cross section
        
        Parameters
        ----------
        E      : array : units = eV
                       incident energy
        
        W      : array : units = eV  
                       energy loss
        
        nfree  : array : units = dim
        
        c_pi_efour: scalar: units = cm**2 * eV**2
        
        Returns
        -------
        dCS_M  : array : units = cm**2  /eV    
    """  
    eps = W*1./E
    dCS_M =  nfree*c_pi_efour* ( 1./(eps**2) + 
                 ( 1./((1.-eps)**2) ) - ( 1./(eps*(1.-eps)) ) )/(E**3)
    
    return dCS_M

#### 2b) Gryzinski differential cross section for core shell electrons

In [27]:
@has_units
def gryz_dCS(E, W, Ebi, nsi, c_pi_efour):
    """ Calculate the Moller inelastic cross section
        
        Parameters
        ----------
        E      : array : units = eV
                       incident energy
                       
        W      : array : units = eV 
                       energy loss
        
        Ebi    : array : units = eV 
                       binding energy of shell i
                
        nsi    : array : units = dim       
                       number of electrons in shell i
        
        c_pi_efour: scalar: units = cm**2 * eV**2
         
        Returns
        -------
        dCS_G    : array : units = cm**2/ eV     
    """ 
    
    eps = W*1./E
    epsB = Ebi*1./E
    
    dCS_G = nsi * c_pi_efour * eps* (1. + epsB)**(-1.5) * (1. - eps)**(epsB/(epsB+eps)) * ( (1. - epsB) +
                               4. * epsB* np.log(2.7 + ((1. - eps)/epsB)**(0.5) )/(3.* eps) )   /(W**3) 
    return dCS_G


In [28]:
w_Moller = UnitArray(np.linspace(10, E_Al/2., 2000), units="eV")
E_dsc = UnitScalar(20000, units="eV")
widths = [3, 2, 1]

t_dCS_M = go.Scatter(
    x = np.array(w_Moller),
    y = np.array(moller_dCS(E_dsc, w_Moller, n_val_Al, c_pi_efour)),
    mode = 'lines', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)

t_dCS_G = []

for indx, Eb in enumerate(list(Ei_Al)):
    w_Gryz = UnitArray(np.linspace(Eb, E_Al, 2000), units="eV")
        
    nameT = "Gryzinski " + name_s_Al[indx]
    t_dCS_G.append(go.Scatter(
        x = np.array(w_Gryz),
        y = np.array(gryz_dCS(E_dsc, w_Gryz, Eb, ni_Al[indx], c_pi_efour)),
        mode = 'lines', 
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                      width = widths[indx]
                     )             
    ))



layout = go.Layout(
    title = 'Al', 
    font=dict( color='#7f7f7f'),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    xaxis=dict(
        #range=[np.log(0.01),np.log(1.2)],
        type='log',
        autorange=True,
        title = 'Energy loss, dE (eV)'
    ), 
    yaxis=dict(
        #type='log',
        autorange=True,
        title = 'd sigma/dE'
    )
)



data = [t_dCS_M, t_dCS_G[0], t_dCS_G[1], t_dCS_G[2]]
#data = [t_dCS_G[0], t_dCS_G[1], t_dCS_G[2]]
fig = go.Figure(data=data, layout=layout)

fig.show()

### Cumulative distribution funciton for excitations

In [29]:
def binEdgePairs(inList):
    ''' For a given list, like the binEdges,
        return list of sets of two edges for each bin
    '''
    outList = [(inList[0], inList[0])]
    for i in range(len(inList)-1):
        outList.append((inList[i], inList[i+1]))
    return outList

def integrand(W, E): return gryz_dCS(E, W, Ei_Al[0], ni_Al[0], c_pi_efour)
#def integrand(W, E): return moller_dCS(E, W, n_val_Al, c_pi_efour)


Wseries = np.geomspace(Ei_Al[0], float(E_Al)-100, 100, dtype=np.float32)
#Wseries = np.linspace(Ei_Al[0], float(E_Al), 100)

intSteps = np.trapz(binEdgePairs(np.array( [float(integrand(W,float(E_Al)-100)) for W in Wseries] )), x=binEdgePairs(Wseries) )


cumSum = np.cumsum(intSteps[:-1])

CDF = cumSum/cumSum[-1]

t_dCDF_M_1 = go.Scatter(
    x = Wseries[1:-1],
    y = CDF,
    mode = 'markers', 
    name = 'CDF Emax-1', 
    #marker = dict(color='#d9f0a3')
)

Wseries = np.geomspace(Ei_Al[0], float(E_Al), 100, dtype=np.float32)
#Wseries = np.linspace(Ei_Al[0], float(E_Al), 100)

intSteps = np.trapz(binEdgePairs(np.array( [float(integrand(W,float(E_Al))) for W in Wseries] )), x=binEdgePairs(Wseries) )


cumSum = np.cumsum(intSteps[:-1])

CDF = cumSum/cumSum[-1]

t_dCDF_M_2 = go.Scatter(
    x = Wseries[1:-1],
    y = CDF,
    mode = 'markers', 
    name = 'CDF Emax', 
    #marker = dict(color='#d9f0a3')
)


data = [t_dCDF_M_1, t_dCDF_M_2]
fig = go.Figure(data=data)

fig.show()


## Stopping power $\frac{d E}{d s}$


#### 2a) Moller stopping power for free electrons

In [30]:
@has_units
def moller_sp(E, Emin, nfree, n, c_pi_efour):
    """ Calculate the Moller stopping power
        
        Parameters
        ----------
        E      : array : units = eV
        
        Emin   : array : units = eV        
        
        nfree  : array : units = dim
        
        n      : array : units = cm**-3
               atom number density
        
        c_pi_efour: scalar: units = cm**2 * eV**2
        
        Returns
        -------
        sp_M   : array : units = eV/angstrom     
    """  
    
    eps = Emin*1./E
    sp_M = nfree*n*c_pi_efour*(2. - (1./(1.-eps)) +  np.log( 1./(8.* eps*((1.-eps)**2)) ))/E  * cm**(-1)/angstrom**(-1) 
    return sp_M

#### 2b) Gryzinski stopping power for core shell electrons

In [31]:
@has_units
def gryz_sp(E, Enl, nsi, n, c_pi_efour):
    """ Calculate the Gryzinski inelastic cross section
        
        Parameters
        ----------
        E      : array : units = eV
        
        Enl    : array : units = eV 
        
        nsi    : array : units = dim
               number of electrons in i-shell
        
        n      : array : units = cm**-3
               atom number density
               
        c_pi_efour: scalar: units = cm**2 * eV**2
         
        Returns
        -------
        s_G    : array : units = eV/angstrom   
    """ 
    
    U = E*1./Enl
    sp_G = nsi * n* c_pi_efour * ((U - 1.)/(U + 1.))**1.5 * (np.log(U) + 
                                     4.*np.log(2.7+(U-1.)**0.5)/3.)/E * cm**(-1)/angstrom**(-1)                                                    
    return sp_G

#### 2c) Quinn stopping power for plasmons

In [32]:
@has_units
def quinn_sp(E, Epl, Ef, n, bohr_r):
    """ Calculate the Quinn inelastic stopping power
        Patrick's formula
        
        Parameters
        ----------
        E      : array : units = eV
                incident energy
                
        Epl    : array : units = eV        
                plasmon energy
        
        Ef     : array : units = eV        
                Fermi energy
                
        n      : array : units = m**-3
               atom number density
        
        bohr_r :scalar : units = m
        
        Returns
        -------
        sp_Q    : array : units = eV/angstrom       
    """     
    E_Ef = E*1./Ef
    Epl_Ef = Epl*1./Ef
    
    s_Q_total = Epl*np.log( ((1. + Epl_Ef)**(0.5) - 1.)/ ( E_Ef**0.5 - 
             (E_Ef - Epl_Ef)**0.5 ) )/(2. *  bohr_r * E) 
    sp_Q = s_Q_total * m**(-1)/ angstrom**(-1) * Epl
    
    return sp_Q

#### 2d) Bethe continuous stopping power

In [33]:
@has_units
def bethe_cl_sp(Z,E,n,c_pi_efour):
    """ Calculate the Bethe continuous inelastic scattering stopping power
        per atom 
        
        Parameters
        ----------
        Z      : array : units = dim
                atomic number
                
        E      : array : units = eV        
                incident energy
        
        n      : array : units = m**-3
               number density
        
        c_pi_efour: scalar: units = cm**2 * eV**2
        
        Returns
        -------
        sp_B    : array : units = eV/angstrom
    """     
    #the mean ionisation potential J in eV
    if (Z>=13):
        J = (9.76*Z + 58.5/(Z**0.19))
    else:
        J = 11.5*Z
        
    sp_B = 2.*c_pi_efour*n*(Z/E) * np.log( 1.166*(E )/J ) * m**-3*cm**2/angstrom**-1
    return sp_B



@has_units
def bethe_mod_sp_k(Z,E,n,k,c_pi_efour):
    """ Calculate the Bethe continuous inelastic scattering stopping power
        per atom 
        
        Parameters
        ----------
        Z      : array : units = dim
                atomic number
                
        E      : array : units = eV        
                incident energy
        
        n      : array : units = m**-3
               number density
        
        c_pi_efour: scalar: units = cm**2 * eV**2
        
        Returns
        -------
        sp_B    : array : units = eV/angstrom
    """     
    #the mean ionisation potential J in eV
    if (Z>=13):
        J = (9.76*Z + 58.5/(Z**0.19))
    else:
        J = 11.5*Z
        
    sp_B = 2.*c_pi_efour*n*(Z/E) * np.log( 1.166*(E + k*J )/J ) * m**-3*cm**2/angstrom**(-1)
    return sp_B


@has_units
def bethe_mod_sp(E,n, Zi, Ei, Zval, Eval, c_pi_efour):
    """ Calculate the Bethe continuous inelastic scattering stopping power
        per atom 
        
        Parameters
        ----------             
        E      : array : units = eV        
                incident energy
        
        n      : array : units = cm**-3
               number density
           
        Zi     : array : units = dim
                occupancy of shell i
                
        Ei     : array : units = eV
                binding energy of shell i        
        
        c_pi_efour: scalar: units = cm**2 * eV**2
        
        Returns
        -------
        sp_B    : array : units = eV/angstrom
    """     

    prefactor = (2.*c_pi_efour*n/E ) * cm**(-1)/angstrom**(-1)
    
    sumi = Zval*np.log(E*1./Eval)
    for indx, Eb in enumerate((Ei)):
        sumi = sumi + Zi[indx]* np.log( E*1./Eb ) 
    
    sp_B = prefactor * sumi
    return sp_B

In [34]:
# stopping power for Si @ 30 kV
n_Si = at_num_dens(density_Si, atwt_Si)

E_Si = UnitScalar(30000, units="eV")
print ('classic', bethe_cl_sp(Z_Si,E_Si,n_Si,c_pi_efour))

print ('JL', bethe_mod_sp_k(Z_Si,E_Si,n_Si,k_Si,c_pi_efour))

classic UnitScalar (eV/angstrom): 0.1614339487780429
JL UnitScalar (eV/angstrom): 0.16157682525121325


In [35]:
sigma_e = UnitArray(np.linspace(Ec_Al, E_Al, 10), units="eV")
n_Al = at_num_dens(density_Al, atwt_Al)
#c_pi_efour = 6.51408491409531e-14
#sigma_e = np.linspace(int(Ec_Al), int(E_Al), 10)
#print n_Al
#print bethe_mod_sp_k(Z_Al, sigma_e[5:], n_Al, k_Al, c_pi_efour)

# @has_units
# def function(a, b):
#     """         
#         Parameters
#         ----------             
#         a : array : units = m        
        
#         b : scalar: units = m
        
#         Returns
#         -------
#         sp_B    : array : units = m
#     """     
#     return a + b
    
    
# #a = UnitScalar(5, units='m')
# #b = UnitScalar(4, units='m')
# a=b=4
# print a+b
#print m**-3 * cm**2/ angstrom**-1    

### Plot stopping powers

#### Al

In [53]:
# array of energies
sigma_e = UnitArray(np.linspace(Ec_Al, 20000, 1000), units="eV")


t_sp_M = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(moller_sp(sigma_e[0:], Ec_Al, n_val_Al, n, c_pi_efour)),
    mode = 'lines', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)

t_sp_G = []
for indx, Eb in enumerate(list(Ei_Al)):
    nameT = "inner shell" + name_s_Al[indx]
    t_sp_G.append(go.Scatter(
        x = np.array(sigma_e[0:]),
        y = np.array(gryz_sp(sigma_e[0:], Ei_Al[indx], ni_Al[indx], n_Al, c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                      width = widths[indx]
                     )
          ))

    
t_sp_Q = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(quinn_sp(sigma_e[0:], Epl, Ef, n_Al, bohr_r)),
    mode = 'lines', 
    name = 'plasmons', 
    marker = dict(color='#fed976')
)

t_sp_Bcl = go.Scatter(
    x = np.array(sigma_e[5:]),
    y = np.array(bethe_cl_sp(Z_Al, sigma_e[5:], n_Al, c_pi_efour)),
    mode = 'lines', 
    name = 'bethe classic', 
    #marker = dict(color='#d9f0a3'
               #)
)  

t_sp_Bmod_k = go.Scatter(
    x = np.array(sigma_e[5:]),
    y = np.array(bethe_mod_sp_k(Z_Al, sigma_e[5:], n_Al, k_Al, c_pi_efour)),
    mode = 'lines', 
    name = 'bethe modified, Joy Luo k', 
    marker = dict(color='#d9f0a3')
) 

t_sp_Bmod = go.Scatter(
    x = np.array(sigma_e[5:]),
    y = np.array(bethe_mod_sp(sigma_e[5:], n_Al, ni_Al, Ei_Al, n_val_Al, E_val_Al, c_pi_efour)),
    mode = 'lines', 
    name = 'bethe modified', 
    marker = dict(color='#fcc5c0')
)

t_sp_cont = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(bethe_cl_sp(Z_Al, sigma_e[15:], n, c_pi_efour)
                 -moller_sp(sigma_e[15:], Ec_Al, n_val_Al, n, c_pi_efour)
                 -gryz_sp(sigma_e[15:], Ei_Al[0], ni_Al[0],n, c_pi_efour)
                 -gryz_sp(sigma_e[15:], Ei_Al[1], ni_Al[1],n, c_pi_efour)
                 -gryz_sp(sigma_e[15:], Ei_Al[2], ni_Al[2],n, c_pi_efour)
                 -quinn_sp(sigma_e[15:], Epl, Ef, n, bohr_r)
                ),
    mode = 'lines', 
    name = 'diff', 
    #marker = dict(color='#d9f0a3'
               #)
)

G_sp_array_0 = np.array(gryz_sp(sigma_e[0:], Ei_Al[0], ni_Al[0], n, c_pi_efour))
G_sp_array_0[np.isnan([i for i in G_sp_array_0])]  = 0. 

G_sp_array_1 = np.array(gryz_sp(sigma_e[0:], Ei_Al[1], ni_Al[1], n, c_pi_efour))
G_sp_array_1[np.isnan([i for i in G_sp_array_1])]  = 0. 

G_sp_array_2 = np.array(gryz_sp(sigma_e[0:], Ei_Al[2], ni_Al[2], n, c_pi_efour))
G_sp_array_2[np.isnan([i for i in G_sp_array_2])]  = 0. 

t_sp_total = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(moller_sp(sigma_e[0:], Ec_Al, n_val_Al, n, c_pi_efour)
                 +G_sp_array_0
                 +G_sp_array_1
                 +G_sp_array_2
                 +quinn_sp(sigma_e[0:], Epl, Ef, n, bohr_r)
                ),
    mode = 'lines', 
    name = 'total discrete', 
    marker = dict(color='#d9f0a3')
)


layout = go.Layout(
    title = 'Al', 
    font=dict( color='#7f7f7f'),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    xaxis=dict(
        gridcolor= '#7f7f7f',
        #range=[np.log(0.01),np.log(1.2)],
        #type='log',
        autorange=True,
        title = 'Energy (eV)'
    ), 
    yaxis=dict(
        gridcolor= '#7f7f7f',
       #type='log',
        autorange=True,
        title = 'dE/ds '
    )
)


data = [t_sp_M, t_sp_G[0],t_sp_G[1], t_sp_G[2], t_sp_Bmod_k, t_sp_Q, t_sp_cont, t_sp_total]
#data = [t_sp_Bcl,t_sp_Bmod, t_sp_Bmod_k, t_sp_total]
fig = go.Figure(data=data, layout=layout)
fig.show()


/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

divide by zero encountered in true_divide

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

invalid value encountered in add

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in power

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in sqrt

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:30: RuntimeWarning:

invalid value encountered in sqrt



#### Si

In [36]:
n_Si = at_num_dens(density_Si, atwt_Si)
Epl_Si =  plasmon_energy(n_Si, n_val_Si, u_hbar, u_me, u_e, u_eps0)
Ef_Si = fermi_energy(n_Si, n_val_Si,u_hbar, u_me)
print (n_Si, n_val_Si, u_hbar, u_me, u_e, u_eps0)
print (Epl_Si)
print (Ef_Si)


UnitScalar (m**-3): 4.996114722025993e+28 4 UnitScalar (J*s): 1.0545718001391127e-34 UnitScalar (kg): 9.10938356e-31 UnitScalar (coulomb): 1.6021766208e-19 UnitScalar (farad*m**-1): 8.854187817620389e-12
UnitScalar (eV): 16.599789282356724
UnitScalar (eV): 12.464196280886211


In [71]:
# array of energies
sigma_e = UnitArray(np.linspace(Ec_Si, 20000, 1000), units="eV")


t_sp_M = go.Scatter(
    x = np.array(sigma_e[0:]/1000),
    y = np.array(moller_sp(sigma_e[0:], Ec_Si, n_val_Si, n, c_pi_efour)),
    mode = 'lines', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)

t_sp_G = []
for indx, Eb in enumerate(list(Ei_Si)):
    nameT = "inner shell" + name_s_Si[indx]
    t_sp_G.append(go.Scatter(
        x = np.array(sigma_e[0:]/1000),
        y = np.array(gryz_sp(sigma_e[0:], Ei_Si[indx], ni_Si[indx], n_Si, c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                      width = widths[indx]
                     )
          ))

    
t_sp_Q = go.Scatter(
    x = np.array(sigma_e[0:]/1000),
    y = np.array(quinn_sp(sigma_e[0:], Epl, Ef, n_Si, bohr_r)),
    mode = 'lines', 
    name = 'plasmons', 
    marker = dict(color='#fed976')
)

t_sp_Bcl = go.Scatter(
    x = np.array(sigma_e[5:]/1000),
    y = np.array(bethe_cl_sp(Z_Al, sigma_e[5:], n_Si, c_pi_efour)),
    mode = 'lines', 
    name = 'bethe classic', 
    #marker = dict(color='#d9f0a3'
               #)
)  

t_sp_Bmod_k = go.Scatter(
    x = np.array(sigma_e[5:]/1000),
    y = np.array(bethe_mod_sp_k(Z_Si, sigma_e[5:], n_Si, k_Si, c_pi_efour)),
    mode = 'lines', 
    name = 'bethe modified, Joy Luo k', 
    #marker = dict(color='#d9f0a3'
               #)
) 

t_sp_Bmod = go.Scatter(
    x = np.array(sigma_e[5:]/1000),
    y = np.array(bethe_mod_sp(sigma_e[5:], n_Si, ni_Si, Ei_Si, n_val_Si, E_val_Si, c_pi_efour)),
    mode = 'lines', 
    name = 'bethe modified', 
    #marker = dict(color='#d9f0a3'
               #)
)

t_sp_cont = go.Scatter(
    x = np.array(sigma_e[0:]/1000),
    y = np.array(bethe_cl_sp(Z_Si, sigma_e[15:], n, c_pi_efour)
                 -moller_sp(sigma_e[15:], Ec_Si, n_val_Si, n, c_pi_efour)
                 -gryz_sp(sigma_e[15:], Ei_Si[0], ni_Si[0],n, c_pi_efour)
                 -gryz_sp(sigma_e[15:], Ei_Si[1], ni_Si[1],n, c_pi_efour)
                 -gryz_sp(sigma_e[15:], Ei_Si[2], ni_Si[2],n, c_pi_efour)
                 -quinn_sp(sigma_e[15:], Epl, Ef, n, bohr_r)
                ),
    mode = 'lines', 
    name = 'diff', 
    #marker = dict(color='#d9f0a3'
               #)
)

G_sp_array_0 = np.array(gryz_sp(sigma_e[0:], Ei_Si[0], ni_Si[0], n, c_pi_efour))
G_sp_array_0[np.isnan([i for i in G_sp_array_0])]  = 0. 

G_sp_array_1 = np.array(gryz_sp(sigma_e[0:], Ei_Si[1], ni_Si[1], n, c_pi_efour))
G_sp_array_1[np.isnan([i for i in G_sp_array_1])]  = 0. 

G_sp_array_2 = np.array(gryz_sp(sigma_e[0:], Ei_Si[2], ni_Si[2], n, c_pi_efour))
G_sp_array_2[np.isnan([i for i in G_sp_array_2])]  = 0. 

t_sp_total = go.Scatter(
    x = np.array(sigma_e[0:]/1000),
    y = np.array(moller_sp(sigma_e[0:], Ec_Si, n_val_Si, n, c_pi_efour)
                 +G_sp_array_0
                 +G_sp_array_1
                 +G_sp_array_2
                 +quinn_sp(sigma_e[0:], Epl, Ef, n, bohr_r)
                ),
    mode = 'lines', 
    name = 'total discrete', 
    #marker = dict(color='#d9f0a3'
               #)
)


layout = go.Layout(
    title = 'Si', 
    width=500, height=600,#showlegend=False,
#     font=dict( color='#7f7f7f'),
#     paper_bgcolor='rgba(0,0,0,0)',
#     plot_bgcolor='rgba(0,0,0,0)',
    xaxis=dict(
        #gridcolor= '#7f7f7f',
        range=[3, 20],
        #type='log',
        #autorange=True,
        title = 'Energy (keV)'
    ), 
    yaxis=dict(
        #gridcolor= '#7f7f7f',
        #type='log',
        range=[-0.2, 1.5],
        #autorange=True,
        title = 'dE/ds (eV/A)'
    )
)


data = [t_sp_M, t_sp_G[0],t_sp_G[1], t_sp_G[2], t_sp_Bmod_k, t_sp_Q, t_sp_total]
#data = [t_sp_Bcl,t_sp_Bmod, t_sp_Bmod_k, t_sp_total]
fig = go.Figure(data=data, layout=layout)
#fig.show()
fig.write_image("images/stopPower_wleg.svg")

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

divide by zero encountered in true_divide

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

invalid value encountered in add

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in power

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in sqrt

/home/elena/anaconda3/envs/mc/lib/python3.7/site-packages/ipykernel_launcher.py:30: RuntimeWarning:

invalid value encountered in sqrt



#### Cu

In [29]:
n_Cu = at_num_dens(density_Cu, atwt_Cu)
Epl_Cu =  plasmon_energy(n_Cu, n_val_Cu, u_hbar, u_me, u_e, u_eps0)
Ef_Cu = fermi_energy(n_Cu, n_val_Cu,u_hbar, u_me)
print n_Cu
print Epl_Cu
print Ef_Cu

UnitScalar (m**-3): 8.49123187592e+28
UnitScalar (eV): 35.8870757402
UnitScalar (eV): 34.8426844383


In [30]:
# array of energies
sigma_e = UnitArray(np.linspace(Ec_Cu, E_Cu, 1000), units="eV")


t_sp_M = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(moller_sp(sigma_e[0:], Ec_Cu, n_val_Cu, n_Cu, c_pi_efour)),
    mode = 'line', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)

t_sp_G = []
widths = [4, 3, 2, 1]

for indx, Eb in enumerate(list(Ei_Cu)):
    nameT = "inner shell" + name_s_Cu[indx]
    t_sp_G.append(go.Scatter(
        x = np.array(sigma_e[0:]),
        y = np.array(gryz_sp(sigma_e[0:], Ei_Cu[indx], ni_Cu[indx],n_Cu, c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                     width = widths[indx]
                     )
          ))

    
t_sp_Q = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(quinn_sp(sigma_e[0:], Epl_Cu, Ef_Cu, n_Cu, bohr_r)),
    mode = 'line', 
    name = 'plasmons', 
    #marker = dict(color='#d9f0a3')
)

t_sp_Bcl = go.Scatter(
    x = np.array(sigma_e[15:]),
    y = np.array(bethe_cl_sp(Z_Cu, sigma_e[15:], n_Cu, c_pi_efour)),
    mode = 'line', 
    name = 'bethe classic', 
    #marker = dict(color='#d9f0a3'
               #)
)  

t_sp_Bmod_k = go.Scatter(
    x = np.array(sigma_e[5:]),
    y = np.array(bethe_mod_sp_k(Z_Cu, sigma_e[5:], n_Cu, k_Cu, c_pi_efour)),
    mode = 'line', 
    name = 'bethe modified, Joy Luo k', 
    #marker = dict(color='#d9f0a3'
               #)
)


t_sp_Bmod = go.Scatter(
    x = np.array(sigma_e[5:]),
    y = np.array(bethe_mod_sp(sigma_e[5:], n_Cu, ni_Cu, Ei_Cu, n_val_Cu, E_val_Cu, c_pi_efour)),
    mode = 'line', 
    name = 'bethe modified', 
    #marker = dict(color='#d9f0a3'
               #)
)


G_sp_array_0 = np.array(gryz_sp(sigma_e[0:], Ei_Cu[0], ni_Cu[0], n_Cu, c_pi_efour))
G_sp_array_0[np.isnan([i for i in G_sp_array_0])]  = 0. 

G_sp_array_1 = np.array(gryz_sp(sigma_e[0:], Ei_Cu[1], ni_Cu[1], n_Cu, c_pi_efour))
G_sp_array_1[np.isnan([i for i in G_sp_array_1])]  = 0. 

G_sp_array_2 = np.array(gryz_sp(sigma_e[0:], Ei_Cu[2], ni_Cu[2], n_Cu, c_pi_efour))
G_sp_array_2[np.isnan([i for i in G_sp_array_2])]  = 0. 

G_sp_array_3 = np.array(gryz_sp(sigma_e[0:], Ei_Cu[3], ni_Cu[3], n_Cu, c_pi_efour))
G_sp_array_3[np.isnan([i for i in G_sp_array_3])]  = 0. 

t_sp_total = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(moller_sp(sigma_e[0:], Ec_Cu, n_val_Cu, n_Cu, c_pi_efour)
                 +G_sp_array_0
                 +G_sp_array_1
                 +G_sp_array_2
                 +G_sp_array_3
                 +quinn_sp(sigma_e[0:], Epl_Cu, Ef_Cu, n_Cu, bohr_r)
                ),
    mode = 'line', 
    name = 'total', 
    #marker = dict(color='#d9f0a3'
               #)
)


layout = go.Layout(
    title = 'Cu', 
    font=dict( color='#7f7f7f'),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    xaxis=dict(
        gridcolor= '#7f7f7f',
        #range=[np.log(0.01),np.log(1.2)],
        type='log',
        autorange=True,
        title = 'Energy (eV)'
    ), 
    yaxis=dict(
        gridcolor= '#7f7f7f',
        type='log',
        autorange=True,
        title = 'dE/ds '
    )
)


#data = [t_sp_M, t_sp_G[0],t_sp_G[1], t_sp_G[2], t_sp_G[3], t_sp_B, t_sp_Q, t_sp_total]
data = [t_sp_Bcl, t_sp_Bmod_k, t_sp_Bmod, t_sp_total]
fig = go.Figure(data=data, layout=layout)

py.iplot(fig, filename='stopping power Si')

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

divide by zero encountered in divide

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

invalid value encountered in add

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in power

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in sqrt

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:30: RuntimeWarning:

invalid value encountered in sqrt



#### Au

In [31]:
n_Au = at_num_dens(density_Au, atwt_Au)
Epl_Au =  plasmon_energy(n_Au, n_val_Au, u_hbar, u_me, u_e, u_eps0)
Ef_Au = fermi_energy(n_Au, n_val_Cu,u_hbar, u_me)
print n_Au
print Epl_Au
print Ef_Au

UnitScalar (m**-3): 5.90085235294e+28
UnitScalar (eV): 29.9164526058
UnitScalar (eV): 27.336378096


In [42]:
# array of energies
sigma_e = UnitArray(np.linspace(Ec_Au, E_Au, 1000), units="eV")


t_sp_M = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(moller_sp(sigma_e[0:], Ec_Au, n_val_Au, n_Au, c_pi_efour)),
    mode = 'line', 
    name = 'free electrons', 
    marker = dict(color='#d9f0a3'
               )
)

t_sp_G = []
widths = [4.5, 4, 3.5, 3, 2.5, 2, 1.5, 1, 0.5]

for indx, Eb in enumerate(list(Ei_Au)):
    nameT = "inner shell" + name_s_Au[indx]
    t_sp_G.append(go.Scatter(
        x = np.array(sigma_e[0:]),
        y = np.array(gryz_sp(sigma_e[0:], Ei_Au[indx], ni_Au[indx],n_Au, c_pi_efour)),
        name = nameT, 
        line = dict(
                     color='#41b6c4', 
                     width = widths[indx]
                     )
          ))

    
t_sp_Q = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(quinn_sp(sigma_e[0:], Epl_Au, Ef_Au, n_Au, bohr_r)),
    mode = 'line', 
    name = 'plasmons', 
    #marker = dict(color='#d9f0a3')
)

t_sp_B = go.Scatter(
    x = np.array(sigma_e[15:]),
    y = np.array(bethe_cl_sp(Z_Au, sigma_e[15:], n_Au, c_pi_efour)),
    mode = 'line', 
    name = 'bethe', 
    #marker = dict(color='#d9f0a3'
               #)
)  



G_sp_array_0 = np.array(gryz_sp(sigma_e[0:], Ei_Au[0], ni_Au[0], n_Au, c_pi_efour))
G_sp_array_0[np.isnan([i for i in G_sp_array_0])]  = 0. 

G_sp_array_1 = np.array(gryz_sp(sigma_e[0:], Ei_Au[1], ni_Au[1], n_Au, c_pi_efour))
G_sp_array_1[np.isnan([i for i in G_sp_array_1])]  = 0. 

G_sp_array_2 = np.array(gryz_sp(sigma_e[0:], Ei_Au[2], ni_Au[2], n_Au, c_pi_efour))
G_sp_array_2[np.isnan([i for i in G_sp_array_2])]  = 0. 

G_sp_array_3 = np.array(gryz_sp(sigma_e[0:], Ei_Au[3], ni_Au[3], n_Au, c_pi_efour))
G_sp_array_3[np.isnan([i for i in G_sp_array_3])]  = 0. 

G_sp_array_4 = np.array(gryz_sp(sigma_e[0:], Ei_Au[4], ni_Au[4], n_Au, c_pi_efour))
G_sp_array_4[np.isnan([i for i in G_sp_array_4])]  = 0. 

G_sp_array_5 = np.array(gryz_sp(sigma_e[0:], Ei_Au[5], ni_Au[5], n_Au, c_pi_efour))
G_sp_array_5[np.isnan([i for i in G_sp_array_3])]  = 0. 

G_sp_array_6 = np.array(gryz_sp(sigma_e[0:], Ei_Au[6], ni_Au[6], n_Au, c_pi_efour))
G_sp_array_6[np.isnan([i for i in G_sp_array_3])]  = 0. 

G_sp_array_7 = np.array(gryz_sp(sigma_e[0:], Ei_Au[7], ni_Au[7], n_Au, c_pi_efour))
G_sp_array_7[np.isnan([i for i in G_sp_array_3])]  = 0. 

t_sp_total = go.Scatter(
    x = np.array(sigma_e[0:]),
    y = np.array(moller_sp(sigma_e[0:], Ec_Au, n_val_Au, n_Au, c_pi_efour)
                 +G_sp_array_0
                 +G_sp_array_1
                 +G_sp_array_2
                 +G_sp_array_3
                 +G_sp_array_4
                 +G_sp_array_5
                 +G_sp_array_6
                 +G_sp_array_7
                 +quinn_sp(sigma_e[0:], Epl_Au, Ef_Au, n_Au, bohr_r)
                ),
    mode = 'line', 
    name = 'total', 
    #marker = dict(color='#d9f0a3'
               #)
)


layout = go.Layout(
    title = 'Au', 
    font=dict( color='#7f7f7f'),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    xaxis=dict(
        gridcolor= '#7f7f7f',
        #range=[np.log(0.01),np.log(1.2)],
        type='log',
        autorange=True,
        title = 'Energy (eV)'
    ), 
    yaxis=dict(
        gridcolor= '#7f7f7f',
        type='log',
        autorange=True,
        title = 'dE/ds '
    )
)


#data = [t_sp_M, t_sp_G[0],t_sp_G[1], t_sp_G[2], t_sp_G[3], t_sp_B, t_sp_Q, t_sp_total]
data = [t_sp_B, t_sp_total]
fig = go.Figure(data=data, layout=layout)

py.iplot(fig, filename='stopping power Si')

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

divide by zero encountered in divide

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning:

invalid value encountered in add

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in power

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning:

invalid value encountered in sqrt

/home/elena/.local/lib/python2.7/site-packages/ipykernel_launcher.py:30: RuntimeWarning:

invalid value encountered in sqrt

